In [1]:
from PIL import Image
import requests
import torch
from torchvision import transforms
from torchvision.transforms.functional import InterpolationMode
import ruamel_yaml as yaml
from models.tag2text import tag2text_caption

device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')



import gradio as gr

image_size = 384


normalize = transforms.Normalize(mean=[0.485, 0.456, 0.406],
                                std=[0.229, 0.224, 0.225])
transform = transforms.Compose([transforms.Resize((image_size, image_size)),transforms.ToTensor(),normalize])



#######Swin Version
pretrained = '/home/notebook/code/personal/S9049611/BLIP/output/blip_tagtotext_14m/blip_tagtotext_encoderdiv_tar_random_swin/caption_coco_finetune_tagparse_tagfinetune_threshold075_bceloss_tagsingle_5e6_epoch19_negative_1_05_pos_1_10/checkpoint_05.pth'

config_file = 'configs/tag2text_caption.yaml'
config = yaml.load(open(config_file, 'r'), Loader=yaml.Loader)


model = tag2text_caption(pretrained=pretrained, image_size=image_size, vit=config['vit'], 
                    vit_grad_ckpt=config['vit_grad_ckpt'], vit_ckpt_layer=config['vit_ckpt_layer'],
                    prompt=config['prompt'],config=config,threshold = 0.75 )

model.eval()
model = model.to(device)




/opt/conda/lib/python3.7/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertModel: ['bert.encoder.layer.2.attention.self.key.bias', 'cls.seq_relationship.weight', 'bert.encoder.layer.5.intermediate.dense.weight', 'cls.predictions.transform.LayerNorm.weight', 'bert.encoder.layer.7.output.dense.weight', 'bert.encoder.layer.10.output.LayerNorm.bias', 'bert.encoder.layer.2.intermediate.dense.bias', 'bert.encoder.layer.6.attention.self.value.weight', 'bert.encoder.layer.5.attention.self.query.bias', 'bert.encoder.layer.8.intermediate.dense.bias', 'bert.encoder.layer.4.output.dense.bias', 'bert.encoder.layer.8.attention.output.dense.weight', 'bert.encoder.layer.8.attention.self.query.bias', 'bert.encoder.layer.4.attention.output.dense

/encoder/layer/0/crossattention/self/query is tied
/encoder/layer/0/crossattention/self/key is tied
/encoder/layer/0/crossattention/self/value is tied
/encoder/layer/0/crossattention/output/dense is tied
/encoder/layer/0/crossattention/output/LayerNorm is tied
/encoder/layer/0/intermediate/dense is tied
/encoder/layer/0/output/dense is tied
/encoder/layer/0/output/LayerNorm is tied
/encoder/layer/1/crossattention/self/query is tied
/encoder/layer/1/crossattention/self/key is tied
/encoder/layer/1/crossattention/self/value is tied
/encoder/layer/1/crossattention/output/dense is tied
/encoder/layer/1/crossattention/output/LayerNorm is tied
/encoder/layer/1/intermediate/dense is tied
/encoder/layer/1/output/dense is tied
/encoder/layer/1/output/LayerNorm is tied
--------------
/home/notebook/code/personal/S9049611/BLIP/output/blip_tagtotext_14m/blip_tagtotext_encoderdiv_tar_random_swin/caption_coco_finetune_tagparse_tagfinetune_threshold075_bceloss_tagsingle_5e6_epoch19_negative_1_05_pos_

In [6]:

def inference(raw_image, input_tag):
    raw_image = raw_image.resize((image_size, image_size))
    # print(type(raw_image))
    image = transform(raw_image).unsqueeze(0).to(device)   
    model.threshold = 0.69
    if input_tag == '' or input_tag == 'none' or input_tag == 'None':
        input_tag_list = None
    else:
        input_tag_list = []
        input_tag_list.append(input_tag.replace(',',' | '))
    # print(input_tag_list)
    with torch.no_grad():


        caption, tag_predict = model.generate(image,tag_input = input_tag_list, return_tag_predict = True)
        if input_tag_list == None:
            tag_1 = tag_predict
            tag_2 = ['none']
        else:
            _, tag_1 = model.generate(image,tag_input = None, return_tag_predict = True)
            tag_2 = tag_predict


        return tag_1[0],tag_2[0],caption[0]

            # return 'caption: '+caption[0], tag_predict[0]


    
# inputs = [gr.inputs.Image(type='pil'),gr.inputs.Radio(choices=['Image Captioning'], type="value", default="Image Captioning", label="Task"),gr.inputs.Textbox(lines=2, label="User Identified Tags (Optional, Enter with commas)"),gr.inputs.Radio(choices=['Beam search','Nucleus sampling'], type="value", default="Beam search", label="Caption Decoding Strategy")]
inputs = [gr.inputs.Image(type='pil'),gr.inputs.Textbox(lines=2, label="User Specified Tags (Optional, Enter with commas)")]

# outputs = gr.outputs.Textbox(label="Output")
# outputs = [gr.outputs.Textbox(label="Image Caption"),gr.outputs.Textbox(label="Identified Tags")]
outputs = [gr.outputs.Textbox(label="Model Identified Tags"),gr.outputs.Textbox(label="User Specified Tags"), gr.outputs.Textbox(label="Image Caption") ]

title = "Tag2Text"
description = "Welcome to Tag2Text demo! (Supported by Fudan University, OPPO Research Institute, International Digital Economy Academy) <br/> Upload your image to get the tags and caption of the image. Optional: You can also input specified tags to get the corresponding caption."

article = "<p style='text-align: center'><a href='' target='_blank'>Tag2Text: Guiding Language-Image Model via Image Tagging</a> | <a href='' target='_blank'>Github Repo</a></p>"

demo = gr.Interface(inference, inputs, outputs, title=title, description=description, article=article, examples=[['images/COCO_val2014_000000483108.jpg',"none"],
                                                                                                                 ['images/COCO_val2014_000000483108.jpg',"electric cable"],
                                                                                                                 ['images/COCO_val2014_000000483108.jpg',"track, train"] ,    
                                                                                                                ])


demo.launch(share=True)
# demo.launch()

Running on local URL:  http://127.0.0.1:7864
Running on public URL: https://a10a3bf9-64b6-49d4.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades (NEW!), check out Spaces: https://huggingface.co/spaces


In [ ]:

def inference(raw_image, input_tag):
    raw_image = raw_image.resize((image_size, image_size))
    # print(type(raw_image))
    image = transform(raw_image).unsqueeze(0).to(device)   
    model.threshold = 0.69
    if input_tag == '' or input_tag == 'none' or input_tag == 'None':
        input_tag_list = None
    else:
        input_tag_list = []
        input_tag_list.append(input_tag.replace(',',' | '))
    # print(input_tag_list)
    with torch.no_grad():


        caption, tag_predict = model.generate(image,tag_input = input_tag_list, return_tag_predict = True)
        if input_tag_list == None:
            tag_1 = tag_predict
            tag_2 = ['none']
        else:
            _, tag_1 = model.generate(image,tag_input = None, return_tag_predict = True)
            tag_2 = tag_predict


        return tag_1[0],tag_2[0],caption[0]

            # return 'caption: '+caption[0], tag_predict[0]


    
# inputs = [gr.inputs.Image(type='pil'),gr.inputs.Radio(choices=['Image Captioning'], type="value", default="Image Captioning", label="Task"),gr.inputs.Textbox(lines=2, label="User Identified Tags (Optional, Enter with commas)"),gr.inputs.Radio(choices=['Beam search','Nucleus sampling'], type="value", default="Beam search", label="Caption Decoding Strategy")]
inputs = [gr.inputs.Image(type='pil'),gr.inputs.Textbox(lines=2, label="User Specified Tags (Optional, Enter with commas)")]

# outputs = gr.outputs.Textbox(label="Output")
# outputs = [gr.outputs.Textbox(label="Image Caption"),gr.outputs.Textbox(label="Identified Tags")]
outputs = [gr.outputs.Textbox(label="Model Identified Tags"),gr.outputs.Textbox(label="User Specified Tags"), gr.outputs.Textbox(label="Image Caption") ]

title = "Tag2Text"
description = "Welcome to Tag2Text demo! (Supported by Fudan University, OPPO Research Institute, International Digital Economy Academy) <br/> Upload your image to get the tags and caption of the image. Optional: You can also input specified tags to get the corresponding caption."

article = "<p style='text-align: center'><a href='' target='_blank'>Tag2Text: Guiding Language-Image Model via Image Tagging</a> | <a href='' target='_blank'>Github Repo</a></p>"

demo = gr.Interface(inference, inputs, outputs, title=title, description=description, article=article, examples=[['images/COCO_val2014_000000551338.jpg',"none"], 
                                                                                                                ['images/COCO_val2014_000000551338.jpg',"fence, sky"],
                                                                                                                # ['images/COCO_val2014_000000551338.jpg',"grass"],
                                                                                                                 ['images/COCO_val2014_000000483108.jpg',"none"],
                                                                                                                 ['images/COCO_val2014_000000483108.jpg',"electric cable"],
                                                                                                                  # ['images/COCO_val2014_000000483108.jpg',"sky, train"],
                                                                                                                 ['images/COCO_val2014_000000483108.jpg',"track, train"] ,    
                                                                                                                 ['images/COCO_val2014_000000483108.jpg',"grass"]     
                                                                                                                ])


demo.launch(share=True)
# demo.launch()